$\newcommand\N{\mathbb N}
\newcommand\Z{\mathbb Z}
\newcommand\Q{\mathbb Q}
\newcommand\R{\mathbb R}
\newcommand\C{\mathbb C}
\newcommand\too\longrightarrow
\renewcommand\phi\varphi
\renewcommand\epsilon\varepsilon
\renewcommand\hat\widehat
\renewcommand\tilde\widetilde
\renewcommand\bar\overline
\newcommand\fl[1]{\left\lfloor #1\right\rfloor}
\newcommand\llbracket{[\![}
\newcommand\rrbracket{]\!]}
\newcommand\bbr[2]{\llbracket #1,#2\rrbracket}
\newcommand\todo{{\bf TODO }}
\newcommand\prob{\mathbb P}
\newcommand\esp{\mathbb E}
\newcommand\var{\mathbb V}
\newcommand\tribu{\mathfrak T}$

# Une (pas si) courte introduction aux fractales de Newton

Marc Lorenzi

15 octobre 2024

In [ ]:
import matplotlib.pyplot as plt
import numpy
import math, cmath

## 1. Les données

Soit $N\ge 2$. On considère le polynôme $P=X^N-1$. Remarquons que $P'=NX^{N-1}$ s'annule en 0. Soit $f:\C^*\too\C$ définie pour tout $z\in\C^*$ par

$$f(z)=z-\frac{P(z)}{P'(z)}.$$

De façon plus explicite,

$$f(z)=z-\frac{z^N-1}{Nz^{N-1}}=\frac{(N-1)z^N+1}{Nz^{N-1}}.$$

Pour tout $z_0\in\C$, soit $(z_n)_{n\in\N}$ la suite définie par son premier terme $z_0$ et la relation de récurrence

$$\forall n\in\N, z_{n+1}=f(z_n).$$

Supposons que la suite $(z_n)_{n\in\N}$ converge vers $\ell\in\C$. Par les opérations sur les limites et le théorème des suites extraites,

$$\ell = \ell-\frac{P(\ell)}{P'(\ell)}$$

et donc $P(\ell)=0$. Autrement dit, $\ell\in\mathcal U_n$, le groupe des racines $n$èmes de l'unité.

In [ ]:
def P(N, z):
    return z ** N - 1

In [ ]:
def f(N, z):
    return ((N - 1) * z ** N + 1) / (N * z ** (N - 1))

Nous allons dans ce qui suit essayer de nous faire une idée de la *dynamique* de $f$. La suite $(z_n)_{n\in\N}$ converge-t-elle ? Si oui, converge-t-elle **vite** ? Et vers **quelle limite** ? Et, au fait, cette suite est-elle **bien définie** ?

Nous allons faire très peu de maths dans ce notebook. Nous nous contenterons de **voir** et de nous poser des **questions**.

## 2. Première vision : vitesse de convergence

Voici une fonction `plot_newton1`. Pour « tout » $x\in[x_{min},x_{max}]$ et « tout » $y\in[y_{min},y_{max}]$, soit $z_0=x+iy$. On évalue $z_k$ pour $k=0,1,2,\ldots$ Quand s'arrête-t-on ? Il y a quatre possibilités :

- $k$ est égal à un nombre maximal d'itérations `niter` fixé par l'utilisateur.
- $z_k=0$. Mieux vaut s'arrêter avant d'avoir une erreur `ZeroDivisionError`.
- $|z_k|$ est très grand (disons plus grand que $10^{10}$).
- $|P(z_k)|$ est très petit (disons plus petit que $10^{-10}$).

On affecte alors au point $z_0$ une couleur qui dépend de $k$. Plus $k$ est grand, plus la couleur est sombre. Autrement dit, les points clairs sont ceux pour lesquels la suite converge « vite », les points sombres sont ceux pour lesquels la suite converge « lentement » ou « pas du tout ».

In [ ]:
def plot_newton1(N, bornes, nz, niter, sz=6):
    fig = plt.figure(figsize=(sz, sz))
    xmin, xmax, ymin, ymax = bornes
    nx, ny = nz
    M = (ny + 1) * [None]
    for i in range(ny + 1): 
        M[i] = (nx + 1) * [0]
    for i in range(ny + 1):
        for j in range(nx + 1):
            x = xmin + j * (xmax - xmin) / nx
            y = ymin + i * (ymax - ymin) / ny
            z = x + 1j * y
            k = 0
            while k < niter and z != 0 and abs(z) < 1e10 and abs(P(N, z)) > 1e-10:
                z = f(N, z)
                k = k + 1
            M[i][j] = math.log(k + 1, 2)
    plt.imshow(M, cmap='Greys', interpolation='bicubic', origin='lower',
              extent=bornes)

Pour nos explications, nous prendrons $N=3$.

In [ ]:
N = 3
plot_newton1(N, (-1.5, 1.5, -1.5, 1.5), (500, 500), 256)
plt.savefig('figures/racines' + str(N) + '.png', bbox_inches='tight')

On obtient une figure compliquée. Sur cette figure, on voit apparaître

- Les racines cubiques de l'unité $1$, $j$, $j^2$, entourées par des patatoïdes clairs. Plus $z_0$ est proche de l'un de ces trois nombres, plus la suite $(z_n)_{n\in\N}$ converge « vite » vers celui-ci.
- Des filets sombres formant une figure très compliquée. Rappelons que « sombre » signifie que la suite $(z_n)_{n\in\N}$ converge très lentement. Ou peut-être diverge-t-elle ? Ou, pire, elle n'est peut-être pas définie : en effet, si $z_n=0$ alors $z_{n+1}$ n'existe pas !
- Des patatoïdes clairs autour de points à l'intérieur des zones délimitées par les filets sombres. Même remarque que pour le premier point. La suite $(z_n)_{n\in\N}$ converge « vite » si $z_0$ est voisin de ces points.

Parfait, nous voyons apparaître des zones où la suite converge vers une racine cubique de l'unité. Mais laquelle ? 1 ? $j$ ? $j^2$ ? Ceci nous amène à la deuxième vision.

## 3. Deuxième vision : bassins d'attraction

Au lieu de colorier les points en teintes de gris, nous allons les colorier avec des couleurs flashy qui dépendent de la limite de la suite. Être « flashy » signifie utiliser une palette fondée sur le modèle de couleurs HSV (Hue, Saturation, Value).

In [ ]:
def plot_newton2(N, bornes, nz, niter, sz=6):
    fig = plt.figure(figsize=(sz, sz))
    racn = [cmath.exp(2j * k * math.pi / N) for k in range(N)]
    xmin, xmax, ymin, ymax = bornes
    nx, ny = nz
    M = (ny + 1) * [None]
    for i in range(ny + 1): 
        M[i] = (nx + 1) * [0]
    for i in range(ny + 1):
        for j in range(nx + 1):
            x = xmin + j * (xmax - xmin) / nx
            y = ymin + i * (ymax - ymin) / ny
            z = x + 1j * y
            k = 0
            while k < niter and z != 0 and abs(z) < 1e10 and abs(P(N, z)) > 1e-10:
                z = f(N, z)
                k = k + 1
            if abs(P(N, z)) < 1e-10:
                for k in range(N):
                    if abs(z - racn[k]) < 1e-5:
                        M[i][j] = k + 1
            else: pass #print('.', end='')
    plt.imshow(M, cmap='hsv', interpolation='bicubic', origin='lower',
              extent=bornes)

In [ ]:
N = 3
plot_newton2(N, (-1.5, 1.5, -1.5, 1.5), (500, 500), 256)
plt.savefig('figures/racines' + str(N) + 'bis.png', bbox_inches='tight')

- En vert, les points $z_0$ tels que $z_n\too 1$. 
- En bleu, les points $z_0$ tels que $z_n\too j$. 
- En rouge, les points $z_0$ tels que $z_n\too j^2$. 

Chacune des zones colorées est ce que l'on appelle le **bassin d'attraction** de la limite correspondante. Ces bassins d'attraction sont des parties du plan extrêmenent compliquées, et leur bord est l'ensemble de filets sombres que nous avions détectés dans notre première vision. 

## 4. Troisième vision : nombres exceptionnels

La suite $(z_n)_{n\in\N}$ peut n'être définie que jusqu'à un certain rang. C'est le cas lorsque l'un des termes de la suite est nul.

**Définition.** Le nombre complexe $z_0$ est *exceptionnel* lorsqu'il existe $n\in\N$ tel que $z_n=0$.

Nous noterons $\mathcal E$ l'ensemble des complexes exceptionnels. Pour tout $z_0\in\mathcal E$, le *rang* de $z_0$ est l'entier $n$ tel que $z_n=0$. Nous le noterons ${\rm rg}(z_0)$. 

Pour tout $z\in\mathcal E$, 

- ${\rm rg}(z)=0$ si et seulement si $z=0$
- Si $z\ne 0$, ${\rm rg}(f(z))={\rm rg}(z)-1$. Dit autrement, chaque itération nous rapproche de la catastrophe, la terrible division par 0.

Pour tout $n\in\N$, soit

$$\mathcal E_n=\{z\in\mathcal E:{\rm rg}(z)=n\}$$

J'ai dit, au début du notebook, « pas de maths ». Alors admettons ! Les ensembles $\mathcal E_n$ sont disjoints deux à deux, non vides, et

$$\mathcal E=\bigcup_{n\in\N}\mathcal E_n$$

Bref, ils forment une partition de $\mathcal E$. On a $\mathcal E_0=\{0\}$ et pour tout $n\in\N^*$, $\mathcal E_n=f^{-1}(\mathcal E_{n-1})$. Ainsi, connaissant $\mathcal E_{n-1}$, on en déduit $\mathcal E_n$ en résolvant une équation (de degré $N$, certes).

Soit $w, z\in\C$. On a $f(z)=w$ si et seulement si

$$Q_w(z)=(N-1)z^N-Nwz^{N-1}+1=0$$

Pour trouver les racines de $Q_w$, nous allons utiliser la fonction `numpy.roots`. Celle-ci prend en paramètre un polynôme donné par la liste de ses coefficients. Par exemple, le polynôme $3X^2+2X+1$ est représenté par la liste $[3,2,1]$. La fonction `roots` renvoie un tableau numpy (`array`) dont les éléments sont les racines cherchées.

In [ ]:
def poly_Q(N, w):
    return [N - 1, -N * w] + (N - 2) * [0] + [1] 

Pour $N=3$, voici les antécédents de 0 par $f$. Les reconnaissez-vous ?

In [ ]:
numpy.roots(poly_Q(3, 0))

La fonction `exceptionnels` renvoie la liste des éléments de $\mathcal E_0\cup\ldots\cup\mathcal E_n$.

In [ ]:
def exceptionnels(N, n):
    s = [0]
    exc = [0]
    for k in range(n):
        s1 = []
        for w in s:
            zs = numpy.roots(poly_Q(N, w))
            for z in zs:
                s1.append(z)
        s = s1
        exc = exc + s
    return exc

Soyons raisonnables pour la valeur de $n$ ! On a $|\mathcal E_0|=1$ et comme une équation de degré $N$ possède en général $N$ racines (pas de maths, pas de maths !), on a pour tout $n\in\N$ (sauf exception, pas de maths, pas de maths !),

$$|\mathcal E_{n+1}|=N|\mathcal E_{n}|$$

Ainsi (suite géométrique),

$$|\mathcal E_{n}|=N^n$$

La fonction `exceptionnels` renvoie donc une liste de taille

$$\sum_{k=0}^n N^k=\frac{N^{n+1}-1}{N-1}$$

Nous éviterons `exceptionnels(10, 10)` ...

In [ ]:
print(exceptionnels(3, 2))

La fonction `plot_complex` dessine une liste de nombres complexes.

In [ ]:
def plot_complex(zs):
    fig = plt.figure(figsize=(6, 6))
    xs = [z.real for z in zs]
    ys = [z.imag for z in zs]
    plt.plot(xs, ys, 'ok', ms=0.2)
    plt.xlim(-1.5, 1.5)
    plt.ylim(-1.5, 1.5)
    plt.grid()

Dessinons les nombres exceptionnels pour $N=3$.

In [ ]:
N = 3
n = math.floor(math.log(1e5) / math.log(N))
print('n =', n)
zs = exceptionnels(N, n)
print('Taille de la liste :', len(zs))
plot_complex(zs)
plt.savefig('figures/racines' + str(N) + 'ter.png', bbox_inches='tight')

Ce que nous voyons mérite deux remarques.

- L'évidence : un nombre exceptionnel ne peut pas appartenir à un bassin d'attraction. Il est donc normal que les nombres exceptionnels soient sur les fameux « filets sombres ».
- La moins évidence : serait-il possible que **tous** les points des filets sombres soient exceptionnels ? En fait, non. En effet, l'ensemble des points exceptionnels est *dénombrable*, alors que les filets sombres, qui sont le bord des trois bassins d'attraction, forment un ensemble de points non dénombrable (pas de maths, pas de maths !). Cependant, le dessin ci-dessus suggère que, peut-être,

**Proposition ?** L'ensemble des points exceptionnels est **dense** dans les filets sombres.

**Démonstration.** Je ne sais même pas si c'est vrai.